In [195]:
import pandas as pd
from io import StringIO
import os
import re
import numpy as np
import subprocess
from sklearn.model_selection import ShuffleSplit
import matplotlib as plt
from collections import defaultdict
import csv
import time
import pickle

[Go load the parsed csv directly](#load_csv)

In [196]:
def save_obj(obj, name ):
    with open('obj/'+ name + '.pkl', 'wb') as f:
        pickle.dump(obj, f, pickle.HIGHEST_PROTOCOL)

def load_obj(name ):
    with open('obj/' + name + '.pkl', 'rb') as f:
        return pickle.load(f)

In [5]:
problem_entries_path = 'problem_entries.txt'
problem_entries=open(problem_entries_path,"r").read().split('\n')

In [6]:
problem_entries

['calum', 'jamesc', 'behzad', 's0343804', 's0346429', 's0451815', 's0455730']

In [7]:
server_path = '/Volumes/Network/courses/sp/data/'

In [8]:
data_path = 'info.txt'
data_file = open(os.path.join(server_path,data_path),"r").read().split('\n')

In [9]:
data_file

['Information about the data. Only isolated English digits data are listed here.',
 '',
 '',
 'Microphone types:',
 '',
 'two types where the micophone could be at a variable distance from the speaker:',
 '"big"    : stand-mounted Sennheiser mikes (good quality)',
 '"small"  : basic Sun lapel type mic (low quality)',
 '',
 'plus various types of headset microphone:',
 '"headset" (medium quality)',
 '"logitech_headset"',
 '"sennheiser_headset"',
 '',
 'plus a variety of other microphone types, described later in this file.',
 '',
 '',
 'Where two microphone names appear (e.g. "headset/big") they are for',
 'train/test data respectively',
 '',
 'Accent types:',
 'SC : native Scottish English speaker',
 'UK : native other British English speaker',
 'AZ : native Australian/NZ speaker',
 'NA : native North American English speaker',
 'NN : non-native',
 '',
 '',
 '=================================================================',
 '',
 'There are known to be some problems with files from t

In [10]:
year_pattern = re.compile("Year*")

In [11]:
entry_pattern = re.compile("[a-z]")

In [12]:
line_pattern = re.compile('[\. a-zA-z]*:+')

In [13]:
data_dict = {}
for line in data_file:
    if year_pattern.match(line):
        year = line.split(" ")[1]
        continue
    if (entry_pattern.match(line) and (not line_pattern.match(line))):
        line = re.split(" +|\t+ *",line)
        if (len(line)>3 and len(line)<7):
            line[3:] = [' '.join(line[3:6])]
            data_dict.setdefault(year,[]).append(line)

In [14]:
data_dict.keys()

dict_keys(['2000-1', '2001-2', '2002-3', '2003-4', '2004-5', '2005-6', '2006-7', '2010-11', '2011-12', '2012-13', '2013-14', '2014-15', '2015-16', '2016-17', '2017-18', '2018-19', '2019-20'])

In [15]:
tuples = []
for key in data_dict.keys():
    entry_num = len(data_dict[key])
    key_list = [key]*entry_num
    index_list = range(entry_num)
    tuples = tuples+(list(zip(key_list,index_list)))

In [16]:
index = pd.MultiIndex.from_tuples(tuples, names=['Year','Index'])

In [17]:
info_df = pd.DataFrame(columns=['Name','Gender','Microphone','Accent'])
for key in data_dict.keys():
    year_df = pd.DataFrame(data_dict[key],columns=['Name','Gender','Microphone','Accent'])
    info_df=info_df.append(year_df)

In [18]:
info_df.index=index

In [19]:
info_df.shape

(504, 4)

In [20]:
gender = info_df.loc['2013-14']['Microphone'].copy(True)
mic = info_df.loc['2013-14']['Accent'].copy(True)
accent = info_df.loc['2013-14']['Gender'].copy(True)
info_df.loc['2013-14']['Microphone']=mic
info_df.loc['2013-14']['Gender']=gender
info_df.loc['2013-14']['Accent']=accent

In [21]:
info_df.loc['2013-14']

Name  Gender                         Microphone Accent
Index                                                            
0      s1312082    Male         logitech_headset Praat Lab     NN
1      s1355318  Female      logitech_headset Audacity Lab     NN
2      s1367766  Female         logitech_headset Praat Lab     NN
3      s1038946    Male         Apple_EarPods Audacity Lab     NN
4      s0950147  Female          iMac_inbuilt Audacity Lab     UK
5      s1336117  Female          iMac_inbuilt Audacity Lab     NN
6      s1036740  Female         logitech_headset Praat Lab     NN
7      s1114083  Female  Acer_v5-571_inbuilt Audacity Home     NA
8      s0927462  Female          iMac_inbuilt Audacity Lab     UK
9      s1006577  Female       Dell_1555_inbuilt Praat Home     UK
10     s1148578  Female         logitech_headset Praat Lab     NN
11     s0946728  Female               iMac_builtin ?? Home     NN
12     s1367454  Female      logitech_headset Audacity Lab     NN
13     s1126144    Male         Behringer_B1 Audacity Home     SC
14     s0934142    Male       Gioteck_EX-02S Audacity Home     UK

In [22]:
for p in problem_entries:
    indexName = info_df[info_df['Name']==p].index
    info_df.drop(indexName,inplace=True)

In [19]:
info_df.to_csv('recording_info.csv')

## Specify the selecting requirements

In [23]:
selection = info_df[~info_df['Gender'].isin(['f','Female'])]['Name'].values

In [21]:
selection

array(['chongh', 'jamesh', 'markm', 'scottn', 'simonk', 'alex',
       'anthonyb', 'benjamin', 'ccb', 'christop', 'colinb', 'davidr',
       'yokong', 'athan', 'davidt', 'guy', 'jose', 'michaelg', 'michaels',
       'ptepper', 'spengler', 'timm', 'wouter', 's0345201', 's9901729',
       's0345701', 's0340933', 's0348129', 's0344328', 's0343559',
       's0345347', 's0343444', 'joshua', 's0343879', 's0343799',
       's0345336', 's0349492', 's9810638', 's0126339', 's0450736',
       's0453481', 's0454291', 's0455511', 's0457086', 'taal11',
       's0235479', 's0565563', 's0451342', 's0672048', 's0677387',
       's0678004', 's0680940', 's0681481', 's0836504', 's1052161',
       's1052483', 's1054017', 's9061219', 's0680570', 's0806577',
       's0824968', 's0832212', 's0833088', 's0927722', 's0940658',
       's1100218', 's1125835', 's1128289', 's1135029', 's1151467',
       's1157551', 's0906559', 's0907414', 's0949139', 's1021894',
       's1200359', 's1250520', 's1261038', 's1312082'

Generate the files for HTK

In [111]:
# Function for writing the List_inti_train list
# `names` is a list of user names selected before
# `path` is the path to the scp file that we want to write to
def prepareInit(names,path):
    print("Preparing training data list...\n")
    with open(path,'w+') as init:
        for name in names:
            print(name)
            init.write("/Volumes/Network/courses/sp/data/mfcc/train/{}_train.mfcc\n".format(name))
    init.close()
    print("Done\n")
def prepareRecog(names,path):
    print("Preparing testing data list...\n")
    with open(path,'w+') as rec:
        for name in names:
            print(name)
            rec.write("/Volumes/Network/courses/sp/data/mfcc/test/{}_test*.mfcc\n".format(name))
    rec.close()
    print("Done\n")
def prepare_res_label(names,path):
    print("Preparing testing master files list...\n")
    with open(path,'w+') as lab:
        for name in names:
            lab.write("/Volumes/Network/courses/sp/data/lab/test/{}_test.mlf\n".format(name))
            print(name)
    lab.close()
    print("Done\n")
def prepare_res_rec(names,recogresult_path,list_path):
    print("Preparing testing recognition results...\n")
    file_names = [rec for rec in os.listdir(recogresult_path) if rec.split('_')[0] in names and len(rec.split('_'))<3 and re.match(('[\w]*test(?=[0-9])'),rec)]
    with open(list_path,'w+') as rec_result:
        for file_name in file_names:
            rec_result.write("../rec/{}\n".format(file_name))
            print(file_name)
    rec_result.close()
    print("Done\n")

In [112]:
# The path for all lists and specific lists
# Path to the directory containing all the recognition results
recogresult = "../rec/"
# Path to the lists for traininig and testing
listpath = "../list/"
initpath = os.path.join(listpath,"list_init_train.scp")
recopath = os.path.join(listpath,"list_recogniser.scp")
labepath = os.path.join(listpath,"list_results_label.scp")
r_repath = os.path.join(listpath,"list_results_rec.scp")

In [272]:
# Set a list for storing running time
times = []

In [280]:
def run_experiment(trn_list,tst_list,proto='5state_MFCC_E_D_A',model='hmm1',acous_fea='MFCC_E_D_A',timeIT=False,beam_width=0):
    """
    Parameter:
    proto: the prototype HMM model for training and testing, e.g. 5state prototype...
    
    model: the model to use for recognition, e.g. hmm0 or hmm1
    
    acous_fea: the acoustic feature to use when parameterizing waveforms
    
    timeit: whether or to time the recognition procedure
    
    beam_width: the beam_width to use in HVite speech recognition
    """
    
    # Set the acoustic feature to do recognition
    
    with open("../resources/CONFIG",'w+') as feature_config:
        feature_config.write("TARGETKIND = {}".format(acous_fea))
    
    feature_config.close()
    
    prepareInit(trn_list,initpath)
    prepareRecog(tst_list,recopath)
    subprocess.call(['../scripts/mmulti_init_train',proto])
    prepare_res_label(tst_list,labepath)
    
    start = time.time()
    subprocess.call(['../scripts/multi_recognise_test_data',model,str(beam_width)])
    end = time.time()
    elapsed_time = end - start
    if timeIT:
        times.append(elapsed_time)
        
    prepare_res_rec(tst_list,recogresult,r_repath)
    result = None
    try:
        result=subprocess.check_output('../scripts/multi_results')        
        result=result.decode("utf-8")
        if(not result):
            print("empty result")
            return None
    except:
        print("bad user {}".format(trn_list))
        return None
    return result
#     result=subprocess.check_output('../scripts/mmulti_recognise_result')
#     print(result)

In [115]:
def parse_result(result):    
    m = re.search('Corr=(.+?),', result)
    if m:
        found = m.group(1)
        print(found)
    return float(found)

## DONE

## Remove users with WER higher than 0%

In [27]:
all_users = info_df['Name'].values;all_users

array(['nicolek', 'chongh', 'jamesh', 'markm', 'scottn', 'simonk',
       'annika', 'beatrice', 'elisabet', 'fionac', 'michele', 'nicola',
       'panagiot', 'sarah', 'sasha', 'alex', 'anthonyb', 'benjamin',
       'ccb', 'christop', 'colinb', 'davidr', 'yokong', 'andra', 'angie',
       'beata', 'efi', 'kateb', 'kelly', 'kit', 'kristina', 'mariza',
       'milena', 'rachel', 'stav', 'unni', 'vwiersma', 'yoko', 'athan',
       'davidt', 'guy', 'jose', 'michaelg', 'michaels', 'ptepper',
       'spengler', 'timm', 'wouter', 's0345201', 's0343373', 's9901729',
       's0345701', 's0345310', 's0340933', 's0341098', 's0348129',
       's0343949', 's0344328', 's0343559', 's0345347', 's0343820',
       's0343444', 'joshua', 's0343879', 's0343799', 's0348176',
       's0349395', 's0345336', 's0349492', 's0339733', 's9810638',
       's0340681', 's0125605', 's0126339', 's0127196', 's0231469',
       's0450736', 's0450918', 's0450928', 's0450990', 's0453481',
       's0453738', 's0453767', 's045

In [28]:
run_experiment(['panagiot'],['panagiot'])

Preparing training data list...

panagiot
Done

Preparing testing data list...

panagiot
Done

Preparing testing master files list...

panagiot
Done

Preparing testing recognition results...

panagiot_test08.rec
panagiot_test09.rec
panagiot_test30.rec
panagiot_test25.rec
panagiot_test10.rec
panagiot_test04.rec
panagiot_test21.rec
panagiot_test05.rec
panagiot_test26.rec
panagiot_test17.rec
panagiot_test19.rec
panagiot_test27.rec
panagiot_test01.rec
panagiot_test11.rec
panagiot_test12.rec
panagiot_test06.rec
panagiot_test29.rec
panagiot_test15.rec
panagiot_test14.rec
panagiot_test18.rec
panagiot_test22.rec
panagiot_test02.rec
panagiot_test07.rec
panagiot_test24.rec
panagiot_test16.rec
panagiot_test23.rec
panagiot_test03.rec
panagiot_test20.rec
panagiot_test13.rec
panagiot_test28.rec
Done



'WORD: %Corr=36.67, Acc=36.67 [H=11, D=0, S=19, I=0, N=30]\n'

In [29]:
bad_users = []
for user in all_users:
    result = run_experiment([user],[user])
    
    if result==None:
        bad_users.append(user)
        continue
    if parse_result(result) < 100:
        bad_users.append(user)
        continue
bad_users

Preparing training data list...

nicolek
Done

Preparing testing data list...

nicolek
Done

Preparing testing master files list...

nicolek
Done

Preparing testing recognition results...

nicolek_test03.rec
nicolek_test23.rec
nicolek_test07.rec
nicolek_test19.rec
nicolek_test11.rec
nicolek_test02.rec
nicolek_test30.rec
nicolek_test14.rec
nicolek_test26.rec
nicolek_test08.rec
nicolek_test01.rec
nicolek_test27.rec
nicolek_test15.rec
nicolek_test16.rec
nicolek_test25.rec
nicolek_test05.rec
nicolek_test10.rec
nicolek_test04.rec
nicolek_test09.rec
nicolek_test12.rec
nicolek_test29.rec
nicolek_test18.rec
nicolek_test28.rec
nicolek_test20.rec
nicolek_test17.rec
nicolek_test13.rec
nicolek_test06.rec
nicolek_test21.rec
nicolek_test24.rec
nicolek_test22.rec
Done

83.33
Preparing training data list...

chongh
Done

Preparing testing data list...

chongh
Done

Preparing testing master files list...

chongh
Done

Preparing testing recognition results...

chongh_test20.rec
chongh_test01.rec
chongh_

nicola
Done

Preparing testing data list...

nicola
Done

Preparing testing master files list...

nicola
Done

Preparing testing recognition results...

nicola_test29.rec
nicola_test20.rec
nicola_test07.rec
nicola_test16.rec
nicola_test11.rec
nicola_test21.rec
nicola_test18.rec
nicola_test28.rec
nicola_test10.rec
nicola_test19.rec
nicola_test25.rec
nicola_test13.rec
nicola_test03.rec
nicola_test08.rec
nicola_test02.rec
nicola_test22.rec
nicola_test04.rec
nicola_test27.rec
nicola_test06.rec
nicola_test23.rec
nicola_test09.rec
nicola_test24.rec
nicola_test05.rec
nicola_test12.rec
nicola_test14.rec
nicola_test17.rec
nicola_test30.rec
nicola_test26.rec
nicola_test15.rec
nicola_test01.rec
Done

96.67
Preparing training data list...

panagiot
Done

Preparing testing data list...

panagiot
Done

Preparing testing master files list...

panagiot
Done

Preparing testing recognition results...

panagiot_test08.rec
panagiot_test09.rec
panagiot_test30.rec
panagiot_test25.rec
panagiot_test10.rec
pan

66.67
Preparing training data list...

yokong
Done

Preparing testing data list...

yokong
Done

Preparing testing master files list...

yokong
Done

Preparing testing recognition results...

yokong_test13.rec
yokong_test18.rec
yokong_test09.rec
yokong_test27.rec
yokong_test22.rec
yokong_test21.rec
yokong_test05.rec
yokong_test02.rec
yokong_test08.rec
yokong_test14.rec
yokong_test10.rec
yokong_test06.rec
yokong_test30.rec
yokong_test04.rec
yokong_test03.rec
yokong_test26.rec
yokong_test07.rec
yokong_test23.rec
yokong_test20.rec
yokong_test19.rec
yokong_test11.rec
yokong_test15.rec
yokong_test24.rec
yokong_test17.rec
yokong_test25.rec
yokong_test28.rec
yokong_test12.rec
yokong_test29.rec
yokong_test16.rec
yokong_test01.rec
Done

100.00
Preparing training data list...

andra
Done

Preparing testing data list...

andra
Done

Preparing testing master files list...

andra
Done

Preparing testing recognition results...

andra_test23.rec
andra_test03.rec
andra_test19.rec
andra_test01.rec
andr

Done

100.00
Preparing training data list...

stav
Done

Preparing testing data list...

stav
Done

Preparing testing master files list...

stav
Done

Preparing testing recognition results...

stav_test24.rec
stav_test01.rec
stav_test20.rec
stav_test15.rec
stav_test14.rec
stav_test23.rec
stav_test17.rec
stav_test27.rec
stav_test08.rec
stav_test11.rec
stav_test19.rec
stav_test02.rec
stav_test18.rec
stav_test30.rec
stav_test03.rec
stav_test13.rec
stav_test12.rec
stav_test16.rec
stav_test10.rec
stav_test26.rec
stav_test29.rec
stav_test28.rec
stav_test04.rec
stav_test21.rec
stav_test07.rec
stav_test06.rec
stav_test05.rec
stav_test25.rec
stav_test09.rec
stav_test22.rec
Done

80.00
Preparing training data list...

unni
Done

Preparing testing data list...

unni
Done

Preparing testing master files list...

unni
Done

Preparing testing recognition results...

unni_test21.rec
unni_test05.rec
unni_test22.rec
unni_test01.rec
unni_test17.rec
unni_test09.rec
unni_test14.rec
unni_test24.rec
unni_te

Done

96.67
Preparing training data list...

timm
Done

Preparing testing data list...

timm
Done

Preparing testing master files list...

timm
Done

Preparing testing recognition results...

timm_test04.rec
timm_test22.rec
timm_test24.rec
timm_test18.rec
timm_test23.rec
timm_test26.rec
timm_test20.rec
timm_test16.rec
timm_test06.rec
timm_test07.rec
timm_test03.rec
timm_test13.rec
timm_test30.rec
timm_test19.rec
timm_test09.rec
timm_test28.rec
timm_test21.rec
timm_test11.rec
timm_test12.rec
timm_test02.rec
timm_test25.rec
timm_test10.rec
timm_test15.rec
timm_test29.rec
timm_test14.rec
timm_test05.rec
timm_test17.rec
timm_test01.rec
timm_test08.rec
timm_test27.rec
Done

100.00
Preparing training data list...

wouter
Done

Preparing testing data list...

wouter
Done

Preparing testing master files list...

wouter
Done

Preparing testing recognition results...

wouter_test23.rec
wouter_test30.rec
wouter_test25.rec
wouter_test14.rec
wouter_test24.rec
wouter_test09.rec
wouter_test04.rec
wou

...

Preparing testing master files list...

s1941395
Done

Preparing testing recognition results...

s1941395_test14.rec
s1941395_test06.rec
s1941395_test21.rec
s1941395_test26.rec
s1941395_test09.rec
s1941395_test17.rec
s1941395_test05.rec
s1941395_test08.rec
s1941395_test04.rec
s1941395_test30.rec
s1941395_test10.rec
s1941395_test02.rec
s1941395_test16.rec
s1941395_test23.rec
s1941395_test19.rec
s1941395_test11.rec
s1941395_test12.rec
s1941395_test07.rec
s1941395_test18.rec
s1941395_test03.rec
s1941395_test20.rec
s1941395_test27.rec
s1941395_test01.rec
s1941395_test24.rec
s1941395_test13.rec
s1941395_test22.rec
s1941395_test15.rec
s1941395_test29.rec
s1941395_test25.rec
s1941395_test28.rec
Done

100.00
Preparing training data list...

s1916940
Done

Preparing testing data list...

s1916940
Done

Preparing testing master files list...

s1916940
Done

Preparing testing recognition results...

s1916940_test15.rec
s1916940_test05.rec
s1916940_test01.rec
s1916940_test14.rec
s1916940_test27.re

Preparing testing master files list...

s1988523
Done

Preparing testing recognition results...

s1988523_test13.rec
s1988523_test01.rec
s1988523_test14.rec
s1988523_test06.rec
s1988523_test29.rec
s1988523_test05.rec
s1988523_test09.rec
s1988523_test20.rec
s1988523_test03.rec
s1988523_test08.rec
s1988523_test28.rec
s1988523_test27.rec
s1988523_test23.rec
s1988523_test07.rec
s1988523_test10.rec
s1988523_test30.rec
s1988523_test12.rec
s1988523_test26.rec
s1988523_test16.rec
s1988523_test22.rec
s1988523_test25.rec
s1988523_test11.rec
s1988523_test24.rec
s1988523_test17.rec
s1988523_test02.rec
s1988523_test18.rec
s1988523_test04.rec
s1988523_test21.rec
s1988523_test19.rec
s1988523_test15.rec
Done

100.00
Preparing training data list...

s2000148
Done

Preparing testing data list...

s2000148
Done

Preparing testing master files list...

s2000148
Done

Preparing testing recognition results...

s2000148_test29.rec
s2000148_test14.rec
s2000148_test01.rec
s2000148_test24.rec
s2000148_test20.re

Preparing testing master files list...

s1764494
Done

Preparing testing recognition results...

s1764494_test07.rec
s1764494_test06.rec
s1764494_test21.rec
s1764494_test20.rec
s1764494_test08.rec
s1764494_test09.rec
s1764494_test30.rec
s1764494_test10.rec
s1764494_test26.rec
s1764494_test22.rec
s1764494_test13.rec
s1764494_test11.rec
s1764494_test15.rec
s1764494_test24.rec
s1764494_test04.rec
s1764494_test02.rec
s1764494_test29.rec
s1764494_test16.rec
s1764494_test01.rec
s1764494_test28.rec
s1764494_test17.rec
s1764494_test19.rec
s1764494_test12.rec
s1764494_test25.rec
s1764494_test23.rec
s1764494_test05.rec
s1764494_test18.rec
s1764494_test27.rec
s1764494_test14.rec
s1764494_test03.rec
Done

86.67
Preparing training data list...

s1735938
Done

Preparing testing data list...

s1735938
Done

Preparing testing master files list...

s1735938
Done

Preparing testing recognition results...

s1735938_test12.rec
s1735938_test01.rec
s1735938_test02.rec
s1735938_test18.rec
s1735938_test29.rec

Preparing testing master files list...

s1940488
Done

Preparing testing recognition results...

s1940488_test15.rec
s1940488_test19.rec
s1940488_test14.rec
s1940488_test10.rec
s1940488_test18.rec
s1940488_test03.rec
s1940488_test08.rec
s1940488_test04.rec
s1940488_test29.rec
s1940488_test28.rec
s1940488_test05.rec
s1940488_test30.rec
s1940488_test13.rec
s1940488_test02.rec
s1940488_test21.rec
s1940488_test12.rec
s1940488_test07.rec
s1940488_test25.rec
s1940488_test23.rec
s1940488_test20.rec
s1940488_test01.rec
s1940488_test09.rec
s1940488_test16.rec
s1940488_test27.rec
s1940488_test26.rec
s1940488_test24.rec
s1940488_test17.rec
s1940488_test06.rec
s1940488_test11.rec
s1940488_test22.rec
Done

96.67
Preparing training data list...

s1306161
Done

Preparing testing data list...

s1306161
Done

Preparing testing master files list...

s1306161
Done

Preparing testing recognition results...

s1306161_test13.rec
s1306161_test08.rec
s1306161_test14.rec
s1306161_test16.rec
s1306161_test23.rec

['nicolek',
 'chongh',
 'markm',
 'beatrice',
 'elisabet',
 'fionac',
 'michele',
 'nicola',
 'panagiot',
 'sarah',
 'sasha',
 'alex',
 'anthonyb',
 'benjamin',
 'christop',
 'colinb',
 'davidr',
 'andra',
 'angie',
 'efi',
 'kateb',
 'kelly',
 'kit',
 'kristina',
 'mariza',
 'milena',
 'stav',
 'unni',
 'vwiersma',
 'yoko',
 'athan',
 'guy',
 'jose',
 'michaelg',
 'ptepper',
 'spengler',
 'wouter',
 's0345201',
 's0343373',
 's9901729',
 's0345701',
 's0345310',
 's0340933',
 's0341098',
 's0345347',
 's0343820',
 's0343444',
 's0343879',
 's0343799',
 's0348176',
 's0349492',
 's0339733',
 's9810638',
 's0340681',
 's0125605',
 's0231469',
 's0450736',
 's0450928',
 's0450990',
 's0453481',
 's0453767',
 's0454417',
 's0454931',
 's0454934',
 's0457086',
 's0235479',
 's0560804',
 's0562500',
 's0563087',
 's0565890',
 's0568074',
 's0570475',
 's0238734',
 's0452991',
 's0672048',
 's0674231',
 's0674876',
 's0678004',
 's0680940',
 's0681481',
 's0815365',
 's0830024',
 's0834892',

In [30]:
len(bad_users)#after modification, should be less bad users

245

In [184]:
len(bad_users)

256

In [31]:
info_df.shape

(498, 4)

In [32]:
for p in bad_users:
    indexName = info_df[info_df['Name']==p].index
    info_df.drop(indexName,inplace=True)

In [94]:
info_df.to_csv('checked_recording_info.csv')

## Delete the users with different traininig and testing equipments

In [250]:
# standardize the accent to SC, UK, AZ, NA, NN
#info_df[info_df.Accent.str.contains('SC')].loc[:,'Accent'].values[7]#='SC'
info_df[info_df.Accent.str.contains('NN Ch')].loc[:,'Accent']

Year     Index
2003-4   7        NN China
2010-11  9        NN China
2011-12  17       NN China
2014-15  27       NN China
2015-16  8        NN China
         11       NN China
         26       NN China
2016-17  12       NN China
         14       NN China
         18       NN China
         21       NN China
         22       NN China
         23       NN China
         43       NN China
2017-18  7        NN China
         21       NN China
         25       NN China
         30       NN China
         38       NN China
         44       NN China
2018-19  0        NN China
         8        NN China
         9        NN China
         10       NN China
         21       NN China
         22       NN Chile
         23       NN China
         25       NN China
         26       NN China
         37       NN China
2019-20  1        NN China
         4        NN China
         10       NN China
         16       NN China
         17       NN China
         19       NN China
         24  

In [249]:
info_df.replace('NN China (MSIGS60)','NN China',inplace=True)

In [362]:
info_df['Microphone'].value_counts()

iMac                                 74
logitech_headset                     58
laptop                               27
headset                              15
big                                  15
sennheiser_headset                    7
apple_iphone_8                        5
apple_headphones                      4
apple_iphone_xr                       3
apple_iphone_x                        2
samsung_galaxy_s8                     2
microsoft_headset                     2
oneplus_5                             1
oneplus_6                             1
iphone_xr                             1
Acer_v5-571_inbuilt Audacity Home     1
Samsung_Galaxy_S6                     1
logitech_noiseless_mic                1
rode_k2                               1
apple_iphone8                         1
samsung_s8                            1
SamsungS7                             1
small                                 1
google_pixel_2_xl                     1
LogitechA-0060A                       1


In [361]:
info_df.replace('MacBook_Pro','laptop',inplace=True)

In [326]:
info_df['Gender'].value_counts()

m    126
f    123
g      2
F      1
?      1
Name: Gender, dtype: int64

In [330]:
info_df.replace('F','f',inplace=True)

In [363]:
info_df[~info_df.Microphone.str.contains('/',regex=True)]
info_df.to_csv('checked_recording_info.csv')

<a id='load_csv'></a>
## Load checked_recording_info.csv back to info_df

In [28]:
info_df = pd.read_csv('checked_recording_info.csv',index_col=['Year','Index'],keep_default_na=False)
info_df.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 253 entries, (2000-1, 3) to (2019-20, 50)
Data columns (total 4 columns):
Name          253 non-null object
Gender        253 non-null object
Microphone    253 non-null object
Accent        253 non-null object
dtypes: object(4)
memory usage: 9.1+ KB


## Exp1 | Testing the model trained on my data with some others data

In [276]:
train = ["s1735938"]
test  = info_df.head(2)['Name'].values
test

array(['jamesh', 'scottn'], dtype=object)

In [281]:
run_experiment(train,test,timeIT=True,beam_width=10.2)

Preparing training data list...

s1735938
Done

Preparing testing data list...

jamesh
scottn
Done

Preparing testing master files list...

jamesh
scottn
Done

Preparing testing recognition results...

jamesh_test09.rec
jamesh_test05.rec
scottn_test03.rec
jamesh_test11.rec
jamesh_test13.rec
jamesh_test24.rec
jamesh_test17.rec
scottn_test01.rec
scottn_test29.rec
jamesh_test07.rec
scottn_test07.rec
jamesh_test27.rec
jamesh_test14.rec
jamesh_test28.rec
scottn_test17.rec
jamesh_test01.rec
scottn_test30.rec
jamesh_test20.rec
jamesh_test12.rec
scottn_test27.rec
jamesh_test06.rec
jamesh_test03.rec
scottn_test06.rec
jamesh_test21.rec
jamesh_test08.rec
scottn_test05.rec
jamesh_test23.rec
scottn_test09.rec
scottn_test12.rec
jamesh_test18.rec
jamesh_test29.rec
jamesh_test16.rec
jamesh_test30.rec
Done



'WORD: %Corr=30.30, Acc=30.30 [H=10, D=0, S=23, I=0, N=33]\n'

## Exp2 | The effect of gender on WER

New idea: train a model on a half of data being female and a half being male with the other attributes that same
test a two testing sets one is female and anoth male but with the same other attributes.

|iMac,China | iMac,NA USA | iMac,England|
|-----------|-------------|---------|
|4|          4|            4|
|4|          4|            4|
            |2|          2|2|

In [81]:
# first try the mic category with the largest count
info_df['Microphone'].value_counts()

iMac                                 74
logitech_headset                     58
laptop                               27
headset                              15
big                                  15
sennheiser_headset                    7
apple_iphone_8                        5
apple_headphones                      4
apple_iphone_xr                       3
samsung_galaxy_s8                     2
apple_iphone_x                        2
microsoft_headset                     2
Samsung_Galaxy_S6                     1
google_pixel_2xl                      1
oneplus_6                             1
headset/big                           1
LogitechA-0060A                       1
iPhone_8                              1
iphone_xr                             1
CAD_U37_USB                           1
Behringer_B1 Audacity Home            1
oneplus_5                             1
logitech_noiseless_mic                1
huawei_p30                            1
apple_iphone_10                       1


In [82]:
info_df[info_df['Microphone']=='iMac']['Accent'].value_counts()

UK                      18
NA                      17
NN China                14
NN Germany               3
NN Netherlands           2
NN Spain (Catalonia)     1
SC                       1
NN Malaysia              1
NN Korea                 1
NN Hong_Kong             1
NN Denmark               1
NN Norway                1
NN HongKong              1
NN Finland               1
NN Cyprus                1
NN Canada Quebec         1
NN Sweden                1
NN France                1
NN Romania               1
NN Austria/Scotland      1
NN                       1
NN Chile                 1
NN Taiwan                1
NN Greece                1
NN Singapore             1
Name: Accent, dtype: int64

In [83]:
info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='NN China')]['Gender'].value_counts()

f    8
m    5
g    1
Name: Gender, dtype: int64

In [84]:
# split iMac, China 2222
trn   = info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='NN China') & (info_df['Gender']=='f')].head(2)
trn   = trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='NN China') & (info_df['Gender']=='m')].head(2))
tst_1 = info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='NN China') & (info_df['Gender']=='f')].tail(2)
tst_2 = info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='NN China') & (info_df['Gender']=='m')].tail(2)
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 4 entries, (2017-18, 7) to (2018-19, 0)
Data columns (total 4 columns):
Name          4 non-null object
Gender        4 non-null object
Microphone    4 non-null object
Accent        4 non-null object
dtypes: object(4)
memory usage: 291.0+ bytes


In [85]:
info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='NA')]['Gender'].value_counts()

f    12
m     5
Name: Gender, dtype: int64

In [86]:
# split iMac, NA 844
trn  =trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='NA') & (info_df['Gender']=='f')].head(2))
trn  =trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='NA') & (info_df['Gender']=='m')].head(2))
tst_1=tst_1.append(info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='NA') & (info_df['Gender']=='f')].tail(2))
tst_2=tst_2.append(info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='NA') & (info_df['Gender']=='m')].tail(2))
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 8 entries, (2017-18, 7) to (2017-18, 8)
Data columns (total 4 columns):
Name          8 non-null object
Gender        8 non-null object
Microphone    8 non-null object
Accent        8 non-null object
dtypes: object(4)
memory usage: 467.0+ bytes


In [87]:
info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('UK'))]['Gender'].value_counts()

m    10
f     8
Name: Gender, dtype: int64

In [88]:
# split iMac, UK Southern 422
trn  =trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='UK') & (info_df['Gender']=='f')].head(4))
trn  =trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='UK') & (info_df['Gender']=='m')].head(4))
tst_1=tst_1.append(info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='UK') & (info_df['Gender']=='f')].tail(4))
tst_2=tst_2.append(info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='UK') & (info_df['Gender']=='m')].tail(4))
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 16 entries, (2017-18, 7) to (2017-18, 34)
Data columns (total 4 columns):
Name          16 non-null object
Gender        16 non-null object
Microphone    16 non-null object
Accent        16 non-null object
dtypes: object(4)
memory usage: 803.0+ bytes


In [89]:
info_df[(info_df['Microphone']=='logitech_headset')]['Accent'].value_counts()

UK                   9
SC                   7
NA                   7
NN Italy             4
NN                   4
NN China             4
NN Germany           4
NN Greece            2
NN India             2
NN Belgium           2
NN Poland            2
NN France            2
NN Kazakhstan        1
NN Japan             1
NN Mexico            1
NN Hungary           1
NN Austria           1
NN Slovakia          1
NN Czech Republic    1
NN Portugal          1
NN Lithuania         1
Name: Accent, dtype: int64

In [90]:
info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('UK'))]['Gender'].value_counts()

f    5
m    4
Name: Gender, dtype: int64

In [91]:
# split logitech_headset, UK 211
trn  =trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='UK') & (info_df['Gender']=='f')].head(2))
trn  =trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='UK') & (info_df['Gender']=='m')].head(2))
tst_1=tst_1.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='UK') & (info_df['Gender']=='f')].tail(2))
tst_2=tst_2.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='UK') & (info_df['Gender']=='m')].tail(2))
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 20 entries, (2017-18, 7) to (2011-12, 16)
Data columns (total 4 columns):
Name          20 non-null object
Gender        20 non-null object
Microphone    20 non-null object
Accent        20 non-null object
dtypes: object(4)
memory usage: 971.0+ bytes


In [92]:
info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NA'))]['Gender'].value_counts()

m    4
f    3
Name: Gender, dtype: int64

In [93]:
# split logitech_headset, NA 211
trn  =trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='NA') & (info_df['Gender']=='f')].head(2))
trn  =trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='NA') & (info_df['Gender']=='m')].head(2))
tst_1=tst_1.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='NA') & (info_df['Gender']=='f')].tail(2))
tst_2=tst_2.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='NA') & (info_df['Gender']=='m')].tail(2))
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 24 entries, (2017-18, 7) to (2011-12, 14)
Data columns (total 4 columns):
Name          24 non-null object
Gender        24 non-null object
Microphone    24 non-null object
Accent        24 non-null object
dtypes: object(4)
memory usage: 1.1+ KB


In [94]:
info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NN China'))]['Gender'].value_counts()

f    3
m    1
Name: Gender, dtype: int64

In [95]:
info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NN Italy'))]['Gender'].value_counts()

f    3
m    1
Name: Gender, dtype: int64

In [96]:
info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NN Germany'))]['Gender'].value_counts()

f    2
m    2
Name: Gender, dtype: int64

In [97]:
trn  =trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='NN Germany') & (info_df['Gender']=='f')].head(1))
trn  =trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='NN Germany') & (info_df['Gender']=='m')].head(1))
tst_1=tst_1.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='NN Germany') & (info_df['Gender']=='f')].tail(1))
tst_2=tst_2.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='NN Germany') & (info_df['Gender']=='m')].tail(1))
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 26 entries, (2017-18, 7) to (2015-16, 6)
Data columns (total 4 columns):
Name          26 non-null object
Gender        26 non-null object
Microphone    26 non-null object
Accent        26 non-null object
dtypes: object(4)
memory usage: 1.2+ KB


In [98]:
info_df[(info_df['Microphone']=='big')]['Accent'].value_counts()

UK              5
NN Pakistan     2
SC              2
NN Belgium      1
NN Finland      1
NN Sweeden      1
NA              1
NN Hong Kong    1
NN Iceland      1
Name: Accent, dtype: int64

In [99]:
info_df[(info_df['Microphone']=='big')&(info_df['Accent']=='UK')]['Gender'].value_counts()

m    5
Name: Gender, dtype: int64

In [100]:
info_df[(info_df['Microphone']=='headset')]['Accent'].value_counts()

NA            4
NN Germany    4
UK            3
NN Spain      1
NN China      1
NN Sweeden    1
NN Poland     1
Name: Accent, dtype: int64

In [101]:
info_df[(info_df['Microphone']=='headset')&(info_df['Accent']=='NN Germany')]['Gender'].value_counts()

f    4
Name: Gender, dtype: int64

In [102]:
trn.to_csv('split/gender_1_Mix50-50_train.csv')
tst_1.to_csv("split/gender_1_female_test.csv")
tst_2.to_csv("split/gender_1_male_test.csv")

In [151]:
trn_usr = trn['Name'].values
tst_usr_1 = tst_1['Name'].values
tst_usr_2 = tst_2['Name'].values

trn_tst_1 = parse_result(run_experiment(trn_usr,tst_usr_1))
trn_tst_2 = parse_result(run_experiment(trn_usr,tst_usr_2))
print(trn_tst_1,trn_tst_2)

Preparing training data list...

s1719048
s1770642
s1718204
s1777759
s1357269
s1313407
s1312747
s1773886
s0950147
s0927462
s1408393
s1531466
s1792565
s1322332
s1783009
s1672756
s0784186
s0830862
s0806577
s1151467
s1159094
s1473254
s1100218
s1128289
s1060613
s1520582
Done

Preparing testing data list...

s1818420
s1879338
s1681275
s1457828
s1408442
s1305077
s1881336
s1879523
s1109026
s1115924
s1473254
s1564606
s1458392
Done

Preparing testing master files list...

s1818420
s1879338
s1681275
s1457828
s1408442
s1305077
s1881336
s1879523
s1109026
s1115924
s1473254
s1564606
s1458392
Done

Preparing testing recognition results...

s1818420_test05.rec
s1564606_test03.rec
s1879338_test27.rec
s1818420_test04.rec
s1879338_test30.rec
s1305077_test23.rec
s1473254_test11.rec
s1305077_test29.rec
s1109026_test25.rec
s1881336_test13.rec
s1564606_test18.rec
s1408442_test14.rec
s1879523_test05.rec
s1818420_test06.rec
s1879523_test18.rec
s1458392_test13.rec
s1115924_test02.rec
s1109026_test20.rec
s187933

92.05
Preparing training data list...

s1719048
s1770642
s1718204
s1777759
s1357269
s1313407
s1312747
s1773886
s0950147
s0927462
s1408393
s1531466
s1792565
s1322332
s1783009
s1672756
s0784186
s0830862
s0806577
s1151467
s1159094
s1473254
s1100218
s1128289
s1060613
s1520582
Done

Preparing testing data list...

s1630726
s1682062
s1832577
s1893594
s0830510
s1885873
s1608591
s1531206
s1574163
s1205542
s1420849
s1567647
s1206798
Done

Preparing testing master files list...

s1630726
s1682062
s1832577
s1893594
s0830510
s1885873
s1608591
s1531206
s1574163
s1205542
s1420849
s1567647
s1206798
Done

Preparing testing recognition results...

s1531206_test07.rec
s1420849_test14.rec
s1574163_test25.rec
s1205542_test25.rec
s1206798_test03.rec
s1832577_test09.rec
s1893594_test21.rec
s1567647_test11.rec
s1205542_test03.rec
s1205542_test22.rec
s1574163_test13.rec
s1893594_test11.rec
s1682062_test09.rec
s1205542_test30.rec
s1574163_test04.rec
s1567647_test37.rec
s0830510_test21.rec
s1885873_test21.rec
s

Done

91.93
92.05 91.93


## Exp3 | Effect of Microphone on the WER
new idea: A model trained on 50/50 far/near (both bad) microphones performs better on a test set recorded far (bad) than a test set recorded close (also bad)

In [152]:
info_df['Microphone'].value_counts()

iMac                                 74
logitech_headset                     58
laptop                               27
headset                              15
big                                  15
sennheiser_headset                    7
apple_iphone_8                        5
apple_headphones                      4
apple_iphone_xr                       3
samsung_galaxy_s8                     2
apple_iphone_x                        2
microsoft_headset                     2
Samsung_Galaxy_S6                     1
google_pixel_2xl                      1
oneplus_6                             1
headset/big                           1
LogitechA-0060A                       1
iPhone_8                              1
iphone_xr                             1
CAD_U37_USB                           1
Behringer_B1 Audacity Home            1
oneplus_5                             1
logitech_noiseless_mic                1
huawei_p30                            1
apple_iphone_10                       1


In [153]:
info_df['Accent'].value_counts()

UK                           51
NA                           47
NN China                     41
NN Germany                   14
SC                           14
NN                            6
NN Italy                      5
NN Denmark                    4
NN Netherlands                4
NN Greece                     4
NN Belgium                    3
NN France                     3
NN Finland                    3
NN Poland                     3
NN Hungary                    2
NN Chile                      2
NN Portugal                   2
NN Sweeden                    2
AZ                            2
NN Germany (macbook)          2
NN India                      2
NN Pakistan                   2
NN Spain                      1
NN Slovakia                   1
NN Hong Kong                  1
NN Ukraine                    1
NN Sweden                     1
NN Denmark (macbook)          1
NN Kazakhstan                 1
Singapore                     1
NN Malaysia                   1
NN Hong_

In [154]:
info_df[info_df['Accent']=='UK']['Gender'].value_counts()

m    29
f    22
Name: Gender, dtype: int64

In [155]:
info_df[(info_df['Accent']=='UK') & (info_df['Gender']=='m')]['Microphone'].value_counts()

iMac                  10
big                    5
logitech_headset       4
laptop                 2
headset                2
apple_headphones       1
iPhone_X               1
samsung_galaxy_s8      1
motorola_moto_g5       1
sennheiser_headset     1
LogitechA-0060A        1
Name: Microphone, dtype: int64

| UK, m         | UK, m | NA,f   | NA,m   |China,f. | China,m |
|---------------|-------|--------|--------|---------|---------|
|8:7iMac,1laptop|4iMac  |8iMac   |3iM,1lap|5iMa,1lap|5iM,3lap |
|4:3iMac,1laptop|2iMac  |4iMac   |2iMac.  |3iMac.   |2iM,2lap |
|4:4logi_head   |2log_h |4hd(l_s)|2hd_lo. |3hd_lo.  |4headset |

In [156]:
# split UK,m
trn= info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='UK') & (info_df['Gender']=='m')].head(3)
trn=trn.append(info_df[(info_df['Microphone']=='headset') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='m')].head(2))
trn=trn.append(info_df[(info_df['Microphone']=='sennheiser_headset') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='m')].head(1))
tst_1 = info_df[(info_df['Microphone']=='iMac') & (info_df['Accent']=='UK') & (info_df['Gender']=='m')].tail(3)
tst_2 = info_df[(info_df['Microphone']=='logitech_headset') & (info_df['Accent']=='UK') & (info_df['Gender']=='m')].head(3)
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 6 entries, (2017-18, 9) to (2010-11, 8)
Data columns (total 4 columns):
Name          6 non-null object
Gender        6 non-null object
Microphone    6 non-null object
Accent        6 non-null object
dtypes: object(4)
memory usage: 383.0+ bytes


In [157]:
info_df[(info_df['Accent']=='UK') & (info_df['Gender']=='f')]['Microphone'].value_counts()

iMac                  8
logitech_headset      5
sennheiser_headset    2
apple_iphone_5s       1
SamsungS7             1
moto_g5               1
apple_iphone_SE       1
google_pixel_2        1
headset               1
apple_iphone_5se      1
Name: Microphone, dtype: int64

In [158]:
trn=trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='f')].head(4))
trn=trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='f')].head(4))
tst_1=tst_1.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='f')].tail(4))
tst_2=tst_2.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='f')].tail(1))
tst_2=tst_2.append(info_df[(info_df['Microphone']=='sennheiser_headset') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='f')].tail(1))
tst_2=tst_2.append(info_df[(info_df['Microphone']=='headset') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='f')].tail(1))
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 14 entries, (2017-18, 9) to (2014-15, 6)
Data columns (total 4 columns):
Name          14 non-null object
Gender        14 non-null object
Microphone    14 non-null object
Accent        14 non-null object
dtypes: object(4)
memory usage: 719.0+ bytes


In [159]:
info_df[info_df['Accent']=='NA']['Gender'].value_counts()

f    29
m    18
Name: Gender, dtype: int64

In [160]:
info_df[(info_df['Accent']=='NA') & (info_df['Gender']=='f')]['Microphone'].value_counts()

iMac                                 12
laptop                                3
logitech_headset                      3
microsoft_headset                     2
samsung_s8                            1
headset                               1
apple_iphone_x                        1
apple_headphones                      1
headset/big                           1
apple_iphone_8                        1
samsung_galaxy_s8                     1
Acer_v5-571_inbuilt Audacity Home     1
sennheiser_headset                    1
Name: Microphone, dtype: int64

In [161]:
trn=trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='f')].head(3))
trn=trn.append(info_df[(info_df['Microphone']=='microsoft_headset') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='f')].head(2))
trn=trn.append(info_df[(info_df['Microphone']=='sennheiser_headset') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='f')].head(1))
tst_1=tst_1.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='f')].tail(3))
tst_2=tst_2.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='f')].tail(3))
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 20 entries, (2017-18, 9) to (2010-11, 7)
Data columns (total 4 columns):
Name          20 non-null object
Gender        20 non-null object
Microphone    20 non-null object
Accent        20 non-null object
dtypes: object(4)
memory usage: 979.0+ bytes


In [162]:
info_df[(info_df['Accent']=='NA') & (info_df['Gender']=='m')]['Microphone'].value_counts()

iMac                   5
logitech_headset       4
headset                3
laptop                 1
big                    1
samsung_galaxy_s10e    1
oneplus_5              1
google_pixel_2xl       1
apple_iphone_7         1
Name: Microphone, dtype: int64

In [163]:
# NA,m 33 3 3
trn  =trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='m')].head(3))
trn  =trn.append(info_df[(info_df['Microphone']=='headset') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='m')].head(3))
tst_1=tst_1.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='m')].tail(2))
tst_1=tst_1.append(info_df[(info_df['Microphone']=='laptop') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='m')].tail(1))
tst_2=tst_2.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='m')].tail(3))

trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 26 entries, (2017-18, 9) to (2006-7, 7)
Data columns (total 4 columns):
Name          26 non-null object
Gender        26 non-null object
Microphone    26 non-null object
Accent        26 non-null object
dtypes: object(4)
memory usage: 1.2+ KB


In [164]:
info_df[info_df['Accent']=='NN China']['Gender'].value_counts()

f    20
m    19
?     1
g     1
Name: Gender, dtype: int64

In [165]:
info_df[(info_df['Accent']=='NN China') & (info_df['Gender']=='f')]['Microphone'].value_counts()

iMac                   8
logitech_headset       3
apple_iphone_8         2
apple_iphone_xr        2
laptop                 1
huawei_p30             1
rode_k2                1
apple_iphone_se        1
apple_iphone_7_plus    1
Name: Microphone, dtype: int64

In [166]:
# China,f 633
trn  =trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NN China')) & (info_df['Gender']=='f')].head(1))
trn  =trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NN China')) & (info_df['Gender']=='f')].head(1))
tst_1=tst_1.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NN China')) & (info_df['Gender']=='f')].tail(1))
tst_2=tst_2.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NN China')) & (info_df['Gender']=='f')].tail(1))
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 28 entries, (2017-18, 9) to (2015-16, 8)
Data columns (total 4 columns):
Name          28 non-null object
Gender        28 non-null object
Microphone    28 non-null object
Accent        28 non-null object
dtypes: object(4)
memory usage: 1.3+ KB


In [167]:
info_df[(info_df['Accent']=='NN China') & (info_df['Gender']=='m')]['Microphone'].value_counts()

laptop                7
iMac                  5
apple_iphone_8        1
logitech_headset      1
apple_iphone_x        1
apple_iphone_X        1
apple_iphone_xr       1
sennheiser_headset    1
headset               1
Name: Microphone, dtype: int64

In [168]:
# China,m 844
trn  =trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NN China')) & (info_df['Gender']=='m')].head(1))
trn  =trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NN China')) & (info_df['Gender']=='m')].head(1))

tst_1=tst_1.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NN China')) & (info_df['Gender']=='m')].tail(1))

tst_2=tst_2.append(info_df[(info_df['Microphone']=='sennheiser_headset') & (info_df.Accent.str.contains('NN China')) & (info_df['Gender']=='m')].tail(1))

trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 30 entries, (2017-18, 9) to (2011-12, 17)
Data columns (total 4 columns):
Name          30 non-null object
Gender        30 non-null object
Microphone    30 non-null object
Accent        30 non-null object
dtypes: object(4)
memory usage: 1.3+ KB


In [169]:
info_df[info_df['Accent']=='SC']['Gender'].value_counts()

m    13
f     1
Name: Gender, dtype: int64

In [170]:
info_df[(info_df['Accent']=='SC') & (info_df['Gender']=='m')]['Microphone'].value_counts()

logitech_headset              6
big                           2
laptop                        1
apple_headphones              1
Behringer_B1 Audacity Home    1
iMac                          1
sennheiser_headset            1
Name: Microphone, dtype: int64

In [171]:
trn  =trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('SC')) & (info_df['Gender']=='m')].head(1))
trn  =trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('SC')) & (info_df['Gender']=='m')].head(1))

tst_1=tst_1.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('SC')) & (info_df['Gender']=='m')].tail(1))

tst_2=tst_2.append(info_df[(info_df['Microphone']=='sennheiser_headset') & (info_df.Accent.str.contains('SC')) & (info_df['Gender']=='m')].tail(1))

trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 32 entries, (2017-18, 9) to (2011-12, 3)
Data columns (total 4 columns):
Name          32 non-null object
Gender        32 non-null object
Microphone    32 non-null object
Accent        32 non-null object
dtypes: object(4)
memory usage: 1.4+ KB


In [172]:
info_df[info_df['Accent']=='NN Germany']['Gender'].value_counts()

f    12
m     2
Name: Gender, dtype: int64

In [173]:
info_df[(info_df['Accent']=='NN Germany') & (info_df['Gender']=='f')]['Microphone'].value_counts()

headset              4
iMac                 3
logitech_headset     2
Samsung_Galaxy_S6    1
apple_iphone_8       1
HUAWEI_nova_2        1
Name: Microphone, dtype: int64

In [174]:
trn  =trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NN Germany')) & (info_df['Gender']=='f')].head(1))
trn  =trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NN Germany')) & (info_df['Gender']=='f')].head(1))

tst_1=tst_1.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NN Germany')) & (info_df['Gender']=='f')].tail(1))

tst_2=tst_2.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NN Germany')) & (info_df['Gender']=='f')].tail(1))

trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 34 entries, (2017-18, 9) to (2010-11, 12)
Data columns (total 4 columns):
Name          34 non-null object
Gender        34 non-null object
Microphone    34 non-null object
Accent        34 non-null object
dtypes: object(4)
memory usage: 1.5+ KB


In [175]:
info_df[(info_df['Accent']=='NN Germany') & (info_df['Gender']=='m')]['Microphone'].value_counts()

logitech_headset    2
Name: Microphone, dtype: int64

In [176]:
trn.to_csv('split/mic_1_far_Mix50-50_train.csv')
tst_1.to_csv("split/mic_1_far_lowQua_test.csv")
tst_2.to_csv("split/mic_1_close_lowQua_test.csv")

In [177]:
trn_usr = trn['Name'].values
tst_usr_1 = tst_1['Name'].values
tst_usr_2 = tst_2['Name'].values

trn_tst_1 = parse_result(run_experiment(trn_usr,tst_usr_1))
trn_tst_2 = parse_result(run_experiment(trn_usr,tst_usr_2))
print(trn_tst_1,trn_tst_2)

Preparing training data list...

s1792565
s1322332
s1783009
s0126339
s0451342
s1052161
s0950147
s0927462
s1408393
s1531466
s0784186
s0830862
s0680304
s1109026
s1357269
s1313407
s1778033
s1564218
s1523985
s1050495
s1312747
s1773886
s1240595
timm
joshua
s0677387
s1719048
s1565865
s1718204
s1157551
s1406597
s0824968
s1444618
s1060613
Done

Preparing testing data list...

s1885873
s1608591
s1531206
s1408442
s1305077
s1881336
s1879523
s1509520
s1681275
s1457828
s1832577
s1893594
s1525891
s1879338
s1682062
s1406597
s1879517
Done

Preparing testing master files list...

s1885873
s1608591
s1531206
s1408442
s1305077
s1881336
s1879523
s1509520
s1681275
s1457828
s1832577
s1893594
s1525891
s1879338
s1682062
s1406597
s1879517
Done

Preparing testing recognition results...

s1531206_test07.rec
s1879338_test27.rec
s1879338_test30.rec
s1305077_test23.rec
s1832577_test09.rec
s1509520_test10.rec
s1305077_test29.rec
s1406597_test12.rec
s1893594_test21.rec
s1881336_test13.rec
s1408442_test14.rec
s1879523_

89.61
Preparing training data list...

s1792565
s1322332
s1783009
s0126339
s0451342
s1052161
s0950147
s0927462
s1408393
s1531466
s0784186
s0830862
s0680304
s1109026
s1357269
s1313407
s1778033
s1564218
s1523985
s1050495
s1312747
s1773886
s1240595
timm
joshua
s0677387
s1719048
s1565865
s1718204
s1157551
s1406597
s0824968
s1444618
s1060613
Done

Preparing testing data list...

s0806577
s1151467
s1574163
s1115924
s0817052
s0127196
s1159094
s1473254
s1564606
s1128289
s1420849
s1567647
s1551548
s1052483
s9061219
s1458392
Done

Preparing testing master files list...

s0806577
s1151467
s1574163
s1115924
s0817052
s0127196
s1159094
s1473254
s1564606
s1128289
s1420849
s1567647
s1551548
s1052483
s9061219
s1458392
Done

Preparing testing recognition results...

s1564606_test03.rec
s1128289_test19.rec
s0817052_test26.rec
s1420849_test14.rec
s1574163_test25.rec
s1052483_test22.rec
s1473254_test11.rec
s0127196_test27.rec
s0806577_test34.rec
s0806577_test21.rec
s1564606_test18.rec
s1567647_test11.rec
s

94.03
89.61 94.03


## Exp4 | Effect of Accent on the WER
#### Hypothesis: Native Accent data has lower error on Naitve accent data than on NN China accent data

In [178]:
info_df['Microphone'].value_counts()

iMac                                 74
logitech_headset                     58
laptop                               27
headset                              15
big                                  15
sennheiser_headset                    7
apple_iphone_8                        5
apple_headphones                      4
apple_iphone_xr                       3
samsung_galaxy_s8                     2
apple_iphone_x                        2
microsoft_headset                     2
Samsung_Galaxy_S6                     1
google_pixel_2xl                      1
oneplus_6                             1
headset/big                           1
LogitechA-0060A                       1
iPhone_8                              1
iphone_xr                             1
CAD_U37_USB                           1
Behringer_B1 Audacity Home            1
oneplus_5                             1
logitech_noiseless_mic                1
huawei_p30                            1
apple_iphone_10                       1


In [179]:
info_df['Accent'].value_counts()

UK                           51
NA                           47
NN China                     41
NN Germany                   14
SC                           14
NN                            6
NN Italy                      5
NN Denmark                    4
NN Netherlands                4
NN Greece                     4
NN Belgium                    3
NN France                     3
NN Finland                    3
NN Poland                     3
NN Hungary                    2
NN Chile                      2
NN Portugal                   2
NN Sweeden                    2
AZ                            2
NN Germany (macbook)          2
NN India                      2
NN Pakistan                   2
NN Spain                      1
NN Slovakia                   1
NN Hong Kong                  1
NN Ukraine                    1
NN Sweden                     1
NN Denmark (macbook)          1
NN Kazakhstan                 1
Singapore                     1
NN Malaysia                   1
NN Hong_

In [180]:
info_df[(info_df['Microphone']=='iMac')]['Gender'].value_counts()

f    43
m    29
g     2
Name: Gender, dtype: int64

In [181]:
info_df[(info_df['Microphone']=='iMac')&(info_df['Gender']=='f')]['Accent'].value_counts()

NA                      12
UK                       8
NN China                 8
NN Germany               3
NN Spain (Catalonia)     1
NN Greece                1
NN Taiwan                1
NN                       1
NN Netherlands           1
NN Austria/Scotland      1
NN Sweden                1
NN Canada Quebec         1
NN HongKong              1
NN Malaysia              1
NN Korea                 1
NN Norway                1
Name: Accent, dtype: int64

In [182]:
# iMac,f NA UK: 5+5,3+3, China:6

trn=info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='f')].head(5)
trn=trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='f')].head(5))
tst_1=info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='f')].tail(3)
tst_1=tst_1.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='f')].tail(3))
tst_2=info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NN China')) & (info_df['Gender']=='f')].tail(6)
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 10 entries, (2017-18, 32) to (2017-18, 48)
Data columns (total 4 columns):
Name          10 non-null object
Gender        10 non-null object
Microphone    10 non-null object
Accent        10 non-null object
dtypes: object(4)
memory usage: 551.0+ bytes


In [183]:
info_df[(info_df['Microphone']=='iMac')&(info_df['Gender']=='m')]['Accent'].value_counts()

UK                10
NN China           5
NA                 5
NN Chile           1
NN Finland         1
NN Romania         1
NN Cyprus          1
SC                 1
NN Hong_Kong       1
NN Denmark         1
NN Netherlands     1
NN Singapore       1
Name: Accent, dtype: int64

In [184]:
# iMac,m 2+2,2,2
trn=trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='m')].head(2))
trn=trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='m')].head(2))
tst_1=trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='m')].tail(1))
tst_1=tst_1.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='m')].tail(1))
tst_2=trn.append(info_df[(info_df['Microphone']=='iMac') & (info_df.Accent.str.contains('NN China')) & (info_df['Gender']=='m')].tail(2))
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 14 entries, (2017-18, 32) to (2017-18, 10)
Data columns (total 4 columns):
Name          14 non-null object
Gender        14 non-null object
Microphone    14 non-null object
Accent        14 non-null object
dtypes: object(4)
memory usage: 719.0+ bytes


In [185]:
info_df[(info_df['Microphone']=='logitech_headset')&(info_df['Gender']=='f')]['Accent'].value_counts()

UK            5
NN            3
NN China      3
NA            3
NN Italy      3
NN Greece     2
NN Germany    2
NN France     1
NN Poland     1
NN Belgium    1
SC            1
NN India      1
NN Austria    1
Name: Accent, dtype: int64

In [186]:
# logitech_headset,f 2+2,1+1,2
# iMac,m 2+2,2,2
trn=trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='m')].head(2))
trn=trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='m')].head(2))
tst_1=trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NA')) & (info_df['Gender']=='m')].tail(1))
tst_1=tst_1.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('UK')) & (info_df['Gender']=='m')].tail(1))
tst_2=trn.append(info_df[(info_df['Microphone']=='logitech_headset') & (info_df.Accent.str.contains('NN China')) & (info_df['Gender']=='m')].tail(2))
trn.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 18 entries, (2017-18, 32) to (2011-12, 16)
Data columns (total 4 columns):
Name          18 non-null object
Gender        18 non-null object
Microphone    18 non-null object
Accent        18 non-null object
dtypes: object(4)
memory usage: 895.0+ bytes


In [187]:
trn.to_csv('split/accent_1_Native_train.csv')
tst_1.to_csv("split/accent_1_Native_test.csv")
tst_2.to_csv("split/accent_1_Chinese_test.csv")

In [190]:
trn_usr = trn['Name'].values
tst_usr_1 = tst_1['Name'].values
tst_usr_2 = tst_2['Name'].values

trn_tst_1 = parse_result(run_experiment(trn_usr,tst_usr_1))
trn_tst_2 = parse_result(run_experiment(trn_usr,tst_usr_2))
print(trn_tst_1,trn_tst_2)

Preparing training data list...

s1357269
s1313407
s1778033
s1873815
s1689291
s0950147
s0927462
s1408393
s1531466
s1408442
s1312747
s1773886
s1792565
s1322332
s1100218
s1128289
s0806577
s1151467
Done

Preparing testing data list...

s1357269
s1313407
s1778033
s1873815
s1689291
s0950147
s0927462
s1408393
s1531466
s1408442
s1312747
s1773886
s1792565
s1322332
s1100218
s1128289
s0806577
s1151467
s1567647
s1205542
Done

Preparing testing master files list...

s1357269
s1313407
s1778033
s1873815
s1689291
s0950147
s0927462
s1408393
s1531466
s1408442
s1312747
s1773886
s1792565
s1322332
s1100218
s1128289
s0806577
s1151467
s1567647
s1205542
Done

Preparing testing recognition results...

s1312747_test10.rec
s1128289_test19.rec
s1322332_test27.rec
s1873815_test08.rec
s1778033_test11.rec
s1205542_test25.rec
s1313407_test24.rec
s1357269_test11.rec
s1408393_test23.rec
s1873815_test16.rec
s1312747_test08.rec
s0927462_test14.rec
s0806577_test34.rec
s0806577_test21.rec
s1778033_test05.rec
s1567647_test

95.96
Preparing training data list...

s1357269
s1313407
s1778033
s1873815
s1689291
s0950147
s0927462
s1408393
s1531466
s1408442
s1312747
s1773886
s1792565
s1322332
s1100218
s1128289
s0806577
s1151467
Done

Preparing testing data list...

s1357269
s1313407
s1778033
s1873815
s1689291
s0950147
s0927462
s1408393
s1531466
s1408442
s1312747
s1773886
s1792565
s1322332
s1100218
s1128289
s0806577
s1151467
s1157551
Done

Preparing testing master files list...

s1357269
s1313407
s1778033
s1873815
s1689291
s0950147
s0927462
s1408393
s1531466
s1408442
s1312747
s1773886
s1792565
s1322332
s1100218
s1128289
s0806577
s1151467
s1157551
Done

Preparing testing recognition results...

s1312747_test10.rec
s1128289_test19.rec
s1322332_test27.rec
s1873815_test08.rec
s1778033_test11.rec
s1313407_test24.rec
s1357269_test11.rec
s1408393_test23.rec
s1873815_test16.rec
s1312747_test08.rec
s0927462_test14.rec
s0806577_test34.rec
s0806577_test21.rec
s1778033_test05.rec
s1312747_test22.rec
s1157551_test28.rec
s0806

95.69
95.96 95.69


## Exp5 | Topology on WER
Divide the data to 2 folds and test the WER with each of the proto-type model. Then loop it for 10 times

In [54]:
rs = ShuffleSplit(n_splits=10, test_size=.5, train_size=.5, random_state=0)
rs.get_n_splits(info_df)
protos = ['3state','4state','5state','6state']
results = defaultdict(list)
print(rs)

for train_index, test_index in rs.split(info_df):
   trn_lst = info_df.iloc[train_index]['Name'].values
   tst_lst = info_df.iloc[test_index]['Name'].values
   for proto in protos:
    result = run_experiment(trn_lst,tst_lst,proto)
    result = parse_result(result)
    results[proto].append(result)
print(results)

ShuffleSplit(n_splits=10, random_state=0, test_size=0.5, train_size=0.5)
Preparing training data list...

s1995221
s0927462
s1941395
s1780852
s1469488
s1444618
s1525891
s0830862
s1406597
s1773886
s1789699
s1241360
s1444568
s1564606
s1531466
s1533593
s1879338
s1872685
s1219096
jamesh
s1423284
s1212806
s1153100
s1159094
s1157551
s1466724
s1766810
s1454439
s0455511
s1511198
s1775230
s1439222
s1564218
s1671123
s1531206
s1926421
beata
s1124728
s1466633
s1451606
s1717837
s1877776
s1621503
s1512295
s1888630
s1520582
s2002376
s0348129
s1616820
s1551548
s0836504
s1367766
s1313407
s1023125
scottn
s1668016
s1604424
s0824968
s1344727
s1649890
s1303513
s0345336
s1052483
s1674500
s1255719
s1532662
s1832577
s1312747
s0817052
s0451342
s1853296
s1354741
s1727834
s1788803
s0679432
s1457828
s1631008
s1826182
s1990816
s1705411
s0784186
s1408442
s1777805
s1796075
s1792565
s0676047
s1876797
s1119520
s1462881
s1706878
s1873815
s1440080
s1451567
s1879517
s1213677
s1322332
s1306161
s1224425
s1420849
s0565246
s

Done

75.63
Preparing training data list...

s1995221
s0927462
s1941395
s1780852
s1469488
s1444618
s1525891
s0830862
s1406597
s1773886
s1789699
s1241360
s1444568
s1564606
s1531466
s1533593
s1879338
s1872685
s1219096
jamesh
s1423284
s1212806
s1153100
s1159094
s1157551
s1466724
s1766810
s1454439
s0455511
s1511198
s1775230
s1439222
s1564218
s1671123
s1531206
s1926421
beata
s1124728
s1466633
s1451606
s1717837
s1877776
s1621503
s1512295
s1888630
s1520582
s2002376
s0348129
s1616820
s1551548
s0836504
s1367766
s1313407
s1023125
scottn
s1668016
s1604424
s0824968
s1344727
s1649890
s1303513
s0345336
s1052483
s1674500
s1255719
s1532662
s1832577
s1312747
s0817052
s0451342
s1853296
s1354741
s1727834
s1788803
s0679432
s1457828
s1631008
s1826182
s1990816
s1705411
s0784186
s1408442
s1777805
s1796075
s1792565
s0676047
s1876797
s1119520
s1462881
s1706878
s1873815
s1440080
s1451567
s1879517
s1213677
s1322332
s1306161
s1224425
s1420849
s0565246
s1718768
s1458392
s1939017
s1881336
s1983536
s1060613
s2000148

s1789553_test24.rec
s1025224_test01.rec
s1893594_test28.rec
s1126144_test39.rec
s1893594_test17.rec
s1523985_test50.rec
s0343559_test05.rec
s0680304_test29.rec
s1464908_test02.rec
timm_test16.rec
s1983839_test10.rec
s1245738_test09.rec
s1778033_test26.rec
s1624468_test12.rec
s1935621_test25.rec
s1232732_test14.rec
s1523985_test02.rec
s1893594_test06.rec
yokong_test21.rec
simonk_test10.rec
s1784888_test21.rec
s1611517_test04.rec
s1682062_test12.rec
s1126144_test37.rec
s1681275_test05.rec
s1679421_test26.rec
s0813426_test02.rec
s0344328_test14.rec
s1624468_test06.rec
s1834488_test24.rec
s1630726_test07.rec
s1681906_test11.rec
s1681275_test12.rec
davidt_test13.rec
s1206798_test26.rec
s1624468_test03.rec
s1025224_test55.rec
s1217013_test12.rec
s1689291_test28.rec
s0126339_test03.rec
s1128289_test15.rec
s1821905_test30.rec
s1305077_test26.rec
s1100218_test27.rec
s1640648_test26.rec
s1128289_test14.rec
s1702630_test16.rec
annika_test07.rec
s1826151_test20.rec
s1933640_test26.rec
timm_test06.

Done

84.82
Preparing training data list...

s1995221
s0927462
s1941395
s1780852
s1469488
s1444618
s1525891
s0830862
s1406597
s1773886
s1789699
s1241360
s1444568
s1564606
s1531466
s1533593
s1879338
s1872685
s1219096
jamesh
s1423284
s1212806
s1153100
s1159094
s1157551
s1466724
s1766810
s1454439
s0455511
s1511198
s1775230
s1439222
s1564218
s1671123
s1531206
s1926421
beata
s1124728
s1466633
s1451606
s1717837
s1877776
s1621503
s1512295
s1888630
s1520582
s2002376
s0348129
s1616820
s1551548
s0836504
s1367766
s1313407
s1023125
scottn
s1668016
s1604424
s0824968
s1344727
s1649890
s1303513
s0345336
s1052483
s1674500
s1255719
s1532662
s1832577
s1312747
s0817052
s0451342
s1853296
s1354741
s1727834
s1788803
s0679432
s1457828
s1631008
s1826182
s1990816
s1705411
s0784186
s1408442
s1777805
s1796075
s1792565
s0676047
s1876797
s1119520
s1462881
s1706878
s1873815
s1440080
s1451567
s1879517
s1213677
s1322332
s1306161
s1224425
s1420849
s0565246
s1718768
s1458392
s1939017
s1881336
s1983536
s1060613
s2000148

s1569669_test05.rec
s1025224_test66.rec
s1355318_test27.rec
s1345679_test30.rec
s1345679_test23.rec
s1114083_test07.rec
s0830510_test17.rec
s0343949_test23.rec
s1679421_test15.rec
s1508979_test28.rec
s1684093_test12.rec
s1523985_test19.rec
s9061219_test14.rec
simonk_test28.rec
s0343949_test02.rec
s1999989_test08.rec
s0949139_test01.rec
s1522469_test28.rec
annika_test15.rec
s1885873_test18.rec
s1834488_test26.rec
s1126144_test24.rec
s0343949_test30.rec
rachel_test08.rec
s1247563_test27.rec
s1783009_test08.rec
s1735938_test22.rec
s1681275_test25.rec
s0565839_test17.rec
s1777759_test03.rec
s1893594_test25.rec
s1834482_test21.rec
yokong_test23.rec
s1265676_test19.rec
s1718204_test03.rec
s1689291_test01.rec
rachel_test30.rec
s1242775_test24.rec
s1888641_test11.rec
s1248784_test20.rec
s1834488_test16.rec
ccb_test11.rec
s1565865_test09.rec
s1682062_test14.rec
s0565839_test14.rec
s1247563_test02.rec
s1473254_test15.rec
s0949139_test09.rec
s1940451_test16.rec
s1826151_test25.rec
s1671540_test27

...

85.87
Preparing training data list...

s1926421
s1789699
s1508979
s1157551
s1212806
s0345336
s1265676
s1567647
s1322332
s0817052
s1684093
s0455511
s1777759
s0454291
s9061219
yokong
s1718768
s1671123
s1564606
s1306782
s1702630
s1443906
s1999989
s1454439
s1879523
s1520582
s1451567
s1248784
s1219096
s1680167
s1778033
s1109026
s1888641
rachel
jamesh
s1306161
s1624468
s1408442
s0349395
timm
s1995898
s1671540
s0343949
s0126339
s1995221
s1881336
s1740779
s1877776
s1423284
s1770642
s1888630
davidt
s1523985
s1826151
s0451342
s1449834
s1720613
s1820672
s1462881
s1532662
s1266927
s1247148
s1571333
s1537176
s1885873
s1727834
s0344328
s1631008
s1604424
s1983536
s1124728
s1988523
s1242775
s1834488
s1060613
s1566512
s1466633
s1672756
s1647760
s1719048
s1983839
s1574163
s1406597
s0679432
s1994964
s1879517
s1336117
s1674500
s1679421
s1904181
s1735938
s1789553
s1509520
s1052483
s0680304
s1681275
s1792565
s1551548
s1312747
s1525891
s1826182
s1788803
s1941395
s1853296
s1818420
s1444568
s0910315
s1916940
s

s0949139_test59.rec
s1466724_test24.rec
s1651681_test07.rec
s1223356_test11.rec
s1668016_test20.rec
michaels_test30.rec
s1531466_test21.rec
s0830510_test13.rec
s1036740_test24.rec
s1204877_test12.rec
s0950147_test09.rec
s1676942_test26.rec
s1796075_test02.rec
s0565246_test05.rec
ccb_test02.rec
s1114083_test27.rec
s1784888_test04.rec
s1255719_test18.rec
s1119520_test27.rec
s1676942_test05.rec
s1832577_test30.rec
s1420849_test26.rec
s1458392_test06.rec
s1939017_test08.rec
s1834482_test18.rec
s1247563_test30.rec
s1682062_test02.rec
s1510868_test23.rec
s1789041_test23.rec
s2002376_test24.rec
s1255719_test01.rec
s1990816_test16.rec
ccb_test07.rec
s1025224_test06.rec
s1512295_test13.rec
s0836504_test16.rec
s1796075_test28.rec
s0348129_test13.rec
s1466724_test27.rec
s1605551_test19.rec
s1783009_test02.rec
s1457828_test19.rec
s1935621_test01.rec
joshua_test30.rec
s1513071_test08.rec
s1464908_test29.rec
s1115924_test29.rec
s0927462_test27.rec
s1153100_test03.rec
s1023125_test14.rec
s1408393_tes

91.21
Preparing training data list...

s1926421
s1789699
s1508979
s1157551
s1212806
s0345336
s1265676
s1567647
s1322332
s0817052
s1684093
s0455511
s1777759
s0454291
s9061219
yokong
s1718768
s1671123
s1564606
s1306782
s1702630
s1443906
s1999989
s1454439
s1879523
s1520582
s1451567
s1248784
s1219096
s1680167
s1778033
s1109026
s1888641
rachel
jamesh
s1306161
s1624468
s1408442
s0349395
timm
s1995898
s1671540
s0343949
s0126339
s1995221
s1881336
s1740779
s1877776
s1423284
s1770642
s1888630
davidt
s1523985
s1826151
s0451342
s1449834
s1720613
s1820672
s1462881
s1532662
s1266927
s1247148
s1571333
s1537176
s1885873
s1727834
s0344328
s1631008
s1604424
s1983536
s1124728
s1988523
s1242775
s1834488
s1060613
s1566512
s1466633
s1672756
s1647760
s1719048
s1983839
s1574163
s1406597
s0679432
s1994964
s1879517
s1336117
s1674500
s1679421
s1904181
s1735938
s1789553
s1509520
s1052483
s0680304
s1681275
s1792565
s1551548
s1312747
s1525891
s1826182
s1788803
s1941395
s1853296
s1818420
s1444568
s0910315
s1916940
s

s1775230_test13.rec
s1309096_test27.rec
s1250520_test29.rec
s0949139_test33.rec
s1357269_test06.rec
s1204877_test04.rec
s1832577_test14.rec
s1050495_test17.rec
s1935621_test14.rec
s1205542_test26.rec
s1025224_test59.rec
s1676942_test22.rec
s1344727_test17.rec
s1569669_test28.rec
s1546267_test28.rec
s1796075_test05.rec
s0838587_test26.rec
s1783009_test17.rec
s1990816_test04.rec
s1345679_test04.rec
s1309096_test12.rec
s0127196_test04.rec
s1682062_test28.rec
s1605551_test02.rec
s1408393_test27.rec
s1773886_test03.rec
s1796075_test04.rec
s1240595_test03.rec
s1621503_test18.rec
s1223356_test30.rec
s1773886_test17.rec
s0676047_test12.rec
s0676047_test28.rec
s1326224_test22.rec
scottn_test12.rec
s1776575_test14.rec
s1444618_test13.rec
s1255719_test19.rec
s0453738_test15.rec
s0950147_test10.rec
s1408393_test11.rec
s1205542_test09.rec
s1303513_test16.rec
s1832577_test02.rec
s1621503_test17.rec
s0830862_test23.rec
s1367766_test14.rec
s1676942_test21.rec
s1616573_test25.rec
s1050495_test02.rec
s1

Done

94.72
defaultdict(<class 'list'>, {'3state': [75.63, 76.52, 77.69, 77.88, 78.19, 76.86, 75.19, 76.48, 78.24, 77.4], '4state': [84.82, 81.96, 88.29, 85.51, 85.85, 85.24, 84.89, 85.83, 87.78, 85.87], '5state': [89.68, 89.91, 91.01, 92.19, 90.54, 91.37, 90.25, 90.62, 91.33, 91.21], '6state': [93.67, 93.83, 94.74, 95.35, 93.81, 94.71, 93.97, 94.88, 94.53, 94.72]})


In [199]:
save_obj(results,"exp5_topo_result")

## Exp6 | Connected Digits -> Done
Change the word insertion penalty

## Exp7 | Baum-Welch training

In [ ]:
rs = ShuffleSplit(n_splits=5, test_size=.5, train_size=.5, random_state=0)
rs.get_n_splits(info_df)
models = ['hmm0','hmm1']
results_hmm = defaultdict(list)
print(rs)

for train_index, test_index in rs.split(info_df):
   trn_lst = info_df.iloc[train_index]['Name'].values
   tst_lst = info_df.iloc[test_index]['Name'].values
   for model in models:
    result = run_experiment(trn_lst,tst_lst,model=model)
    result = parse_result(result)
    results_hmm[proto].append(result)
print(results_hmm)

save_obj(results_hmm,"exp7_models_result")

ShuffleSplit(n_splits=5, random_state=0, test_size=0.5, train_size=0.5)
Preparing training data list...

s1995221
s0927462
s1941395
s1780852
s1469488
s1444618
s1525891
s0830862
s1406597
s1773886
s1789699
s1241360
s1444568
s1564606
s1531466
s1533593
s1879338
s1872685
s1219096
jamesh
s1423284
s1212806
s1153100
s1159094
s1157551
s1466724
s1766810
s1454439
s0455511
s1511198
s1775230
s1439222
s1564218
s1671123
s1531206
s1926421
beata
s1124728
s1466633
s1451606
s1717837
s1877776
s1621503
s1512295
s1888630
s1520582
s2002376
s0348129
s1616820
s1551548
s0836504
s1367766
s1313407
s1023125
scottn
s1668016
s1604424
s0824968
s1344727
s1649890
s1303513
s0345336
s1052483
s1674500
s1255719
s1532662
s1832577
s1312747
s0817052
s0451342
s1853296
s1354741
s1727834
s1788803
s0679432
s1457828
s1631008
s1826182
s1990816
s1705411
s0784186
s1408442
s1777805
s1796075
s1792565
s0676047
s1876797
s1119520
s1462881
s1706878
s1873815
s1440080
s1451567
s1879517
s1213677
s1322332
s1306161
s1224425
s1420849
s0565246
s1

s1036740_test14.rec
s1624468_test10.rec
s1778033_test23.rec
s0680304_test04.rec
s1878472_test14.rec
s1935621_test22.rec
joshua_test03.rec
s0680304_test21.rec
s1988523_test08.rec
s1326224_test20.rec
s1879088_test01.rec
simonk_test23.rec
s0830510_test05.rec
s1818420_test13.rec
s1336117_test12.rec
s1115924_test30.rec
s1206798_test25.rec
s1784888_test13.rec
s0127196_test11.rec
s1217013_test14.rec
s0565563_test25.rec
s1204698_test09.rec
s1336117_test30.rec
s1546267_test03.rec
s1247563_test22.rec
s0565563_test06.rec
s1933640_test24.rec
s1309096_test03.rec
s1672756_test26.rec
joshua_test06.rec
s0127196_test16.rec
s1443906_test08.rec
s1126144_test30.rec
ccb_test15.rec
s1309096_test09.rec
s1888641_test27.rec
s1821905_test02.rec
s0343949_test22.rec
s0940658_test06.rec
s1821905_test13.rec
s0343559_test01.rec
s1608591_test17.rec
s1988523_test28.rec
s1115924_test09.rec
s1778033_test01.rec
s1995898_test16.rec
s1826151_test26.rec
ccb_test12.rec
s1100218_test13.rec
s1522469_test14.rec
s1995898_test29.

89.45
Preparing training data list...

s1995221
s0927462
s1941395
s1780852
s1469488
s1444618
s1525891
s0830862
s1406597
s1773886
s1789699
s1241360
s1444568
s1564606
s1531466
s1533593
s1879338
s1872685
s1219096
jamesh
s1423284
s1212806
s1153100
s1159094
s1157551
s1466724
s1766810
s1454439
s0455511
s1511198
s1775230
s1439222
s1564218
s1671123
s1531206
s1926421
beata
s1124728
s1466633
s1451606
s1717837
s1877776
s1621503
s1512295
s1888630
s1520582
s2002376
s0348129
s1616820
s1551548
s0836504
s1367766
s1313407
s1023125
scottn
s1668016
s1604424
s0824968
s1344727
s1649890
s1303513
s0345336
s1052483
s1674500
s1255719
s1532662
s1832577
s1312747
s0817052
s0451342
s1853296
s1354741
s1727834
s1788803
s0679432
s1457828
s1631008
s1826182
s1990816
s1705411
s0784186
s1408442
s1777805
s1796075
s1792565
s0676047
s1876797
s1119520
s1462881
s1706878
s1873815
s1440080
s1451567
s1879517
s1213677
s1322332
s1306161
s1224425
s1420849
s0565246
s1718768
s1458392
s1939017
s1881336
s1983536
s1060613
s2000148
s1879

## Exp8 | acoustic features

In [ ]:
rs = ShuffleSplit(n_splits=3, test_size=.5, train_size=.5, random_state=0)
rs.get_n_splits(info_df)
features = ['MFCC','MFCC_E','MFCC_E_D','MFCC_E_D_A']
protos = ['5state_MFCC',"5state_MFCC_E","5state_MFCC_E_D","5state_MFCC_E_D_A"]
results_fea = defaultdict(list)
print(rs)

for train_index, test_index in rs.split(info_df):
   trn_lst = info_df.iloc[train_index]['Name'].values
   tst_lst = info_df.iloc[test_index]['Name'].values
   for f,p in zip(features,protos):
    result = run_experiment(trn_lst,tst_lst,acous_fea=f,proto=p)
    result = parse_result(result)
    results_fea[feature].append(result)
print(results_fea)

save_obj(results_fea,"exp8_features_result")

## Exp9 | Among of data

## Exp 10 | Pruning width

In [ ]:
rs = ShuffleSplit(n_splits=1, test_size=.5, train_size=.5, random_state=0)
rs.get_n_splits(info_df)
beam_widths = np.logspace(3,10,10,base=2)
results_prun = defaultdict(list)
print(rs)
times=[]
for train_index, test_index in rs.split(info_df):
   trn_lst = info_df.iloc[train_index]['Name'].values
   tst_lst = info_df.iloc[test_index]['Name'].values
   for beam_width in beam_widths:
    result = run_experiment(trn_lst,tst_lst,timeIT=True,beam_width=beam_width)
    result = parse_result(result)
    results_prun[feature].append(result)
print(results_fea)

save_obj(results_fea,"exp10_pruning_result")
save_obj(times,"exp10_pruning_times")